In [134]:
import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
import numpy as np
import pandas as pd
import textwrap
from pprint import pprint
import os
import re
import data_processing
nltk.download('punkt')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\arthu\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [135]:
import importlib
importlib.reload(data_processing)

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\arthu\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


<module 'data_processing' from 'c:\\Users\\arthu\\Desktop\\ner-using-bert\\BERT_Experiment\\data_processing.py'>

In [136]:
path_to_test = "acerpi_dataset/test/"
path_to_train = "acerpi_dataset/train/"

#### Open Unannotated Documents
We get the unnanotatted texts and store each document as a key, value pair in a dictionary

In [137]:
documents = {}
# Get test documents that require manual labeling
#ALREADY LABELED
# for filename in os.listdir(path_to_test):
#    if filename.endswith(".txt"):
#       with open(os.path.join(path_to_test, filename), 'r', encoding="utf8") as f:
#          key = int(filename.replace('.txt', ''))
#          value = f.read()
#          documents[key] = value

# Get train documents that require manual labeling
for filename in os.listdir(path_to_train):
   if filename.endswith(".txt"):
      with open(os.path.join(path_to_train, filename), 'r', encoding="utf8") as f:
         key = int(filename.replace('.txt', ''))
         value = f.read()
         documents[key] = value

Next we store the documents in a DataFrame

In [138]:
df_docs = pd.DataFrame.from_dict(documents, orient='index')
df_docs.columns = ['text']
print(df_docs.shape)
df_docs.head()

(538, 1)


text
25644  Documento gerado sob autenticação Nº AHX.976.775.357, disponível no endereço\nhttp://www.ufrgs.br/autenticacao\nDocumento certificado eletronicamente, conforme Portaria nº\n3362/2016, que institui o Sistema de Documentos Eletrônicos da UFRGS.\n1/1\nPORTARIA Nº             5866                  de  08/08/2016\nO PRÓ-REITOR DE GESTÃO DE PESSOAS DA UNIVERSIDADE FEDERAL DO RIO GRANDE DO SUL, no\nuso de suas atribuições, considerando o disposto na Portaria nº 5469, de 04 de outubro de 2012\nRESOLVE\nConceder à servidora LISIANE RAMOS VILK, ocupante do cargo de  Administrador de Edifícios -\n701400, lotada na Faculdade de Arquitetura, SIAPE 2325261, o percentual de 25% (vinte e cinco por cento) de\nIncentivo à Qualificação, a contar de 15/07/2016, tendo em vista a conclusão do curso de Graduação em\nAdministração - Bacharelado, conforme o Processo nº 23078.015333/2016-19.\nMAURÍCIO VIÉGAS DA SILVA\nPró-Reitor de Gestão de Pessoas\n
25645  Documento gerado sob autenticação Nº SDG.667.383.ILF, disponível no endereço\nhttp://www.ufrgs.br/autenticacao\nDocumento certificado eletronicamente, conforme Portaria nº\n3362/2016, que institui o Sistema de Documentos Eletrônicos da UFRGS.\n1/1\nPORTARIA Nº             5890                  de  09/08/2016\nO REITOR  DA UNIVERSIDADE FEDERAL DO RIO GRANDE DO SUL, no uso de suas atribuições legais e\nestatutárias\nRESOLVE\nAutorizar  o  afastamento  do  país  de  CRISTINE  MARIA  WARMLING,  Professor  do  Magistério\nSuperior,  lotada e em exercício no Departamento de Odontologia Preventiva e Social  da Faculdade de\nOdontologia, com a finalidade de participar do "3ème Congrès de la Societé Internationale d'Ergologie", em\nAix-en-Provence - França, no período compreendido entre 28/08/2016 e 01/09/2016, com ônus limitado.\nSolicitação nº 19960.\nCARLOS ALEXANDRE NETTO\nReitor\n                                                  
25646  Documento gerado sob autenticação Nº ASL.670.441.ILF, disponível no endereço\nhttp://www.ufrgs.br/autenticacao\nDocumento certificado eletronicamente, conforme Portaria nº 3362/2016,\nque institui o Sistema de Documentos Eletrônicos da UFRGS.\n1/1\nPORTARIA Nº             5891                  de  09/08/2016\nO REITOR  DA UNIVERSIDADE FEDERAL DO RIO GRANDE DO SUL, no uso de suas atribuições legais e\nestatutárias\nRESOLVE\nAutorizar o afastamento do país de ANDRE DIAS MORTARI, Assistente em Administração, lotado e\nem exercício na Escola de Administração, com a finalidade de participar do "IV Congreso Internacional Red\nPilares", em Cartagena - Colombia, no período compreendido entre 29/08/2016 e 02/09/2016, com ônus\nlimitado. Solicitação nº 21766.\nCARLOS ALEXANDRE NETTO\nReitor\n                                                                                                                                                  
25647  Documento gerado sob autenticação Nº PUG.672.561.ILF, disponível no endereço\nhttp://www.ufrgs.br/autenticacao\nDocumento certificado eletronicamente, conforme Portaria nº\n3362/2016, que institui o Sistema de Documentos Eletrônicos da UFRGS.\n1/1\nPORTARIA Nº             5892                  de  09/08/2016\nO REITOR  DA UNIVERSIDADE FEDERAL DO RIO GRANDE DO SUL, no uso de suas atribuições legais e\nestatutárias\nRESOLVE\nAutorizar o afastamento do país de RAFAEL ROESLER, Professor do Maigstério Superior, lotado e\nem exercício no Departamento de Farmacologia do Instituto de Ciências Básicas da Saúde, com a finalidade\nde  participar  de  reunião  na  University  of  Nottingham  -  Inglaterra,  no  período  compreendido  entre\n02/09/2016 e 10/09/2016, com limitado. Solicitação nº 21497.\nCARLOS ALEXANDRE NETTO\nReitor\n                                                                                                          
25648  Documento gerado sob autenticação Nº ORY.674.668.ILF, disponível no endereço\nhttp://www.ufrgs.br/autenticacao\nDocumento certificado eletronicamente, conforme Portaria nº\n3362/2016, que institui o S

#### Data Cleaning
We will use the **data_processing.clear_text** function which was built to clean the specific document we are using here. Since we already know they will be used for NER, the objective of the cleaning is getting the text into a format which will be easy to split into sentences. Each sentence will later be used as an input to our neural network.
There are three aspects we are cleaning:
1. Removing line breaks as they make it very hard for the sentence tokenizer to correctly recognize the begining and ending of sentences in the text
2. Removing repeated whitespaces which are used for the visual formatting of the documents but will generate unnecessary tokens for our neural network.
3. There are a lot of law and document numbers in this documents. There isn't a consistent writing of these numbers which can start as "nº.123", "nº. 123" and "nº 123". We will padronize this occurences to appear as "nº 123" since the punctuation after "nº" makes it harder for the sentence tokenizer to correctly separate the sentences.

In [139]:
df_docs.loc[55505]['text']

'Documento gerado sob autenticação Nº RRM.458.680.FGN, disponível no\nendereço http://www.ufrgs.br/autenticacao\nDocumento certificado eletronicamente, conforme Portaria nº\n3362/2016, que institui o Sistema de Documentos Eletrônicos da UFRGS.\n1/1\nPORTARIA Nº             4534                  de  22/06/2018\nO PRÓ-REITOR DE PLANEJAMENTO E ADMINISTRAÇÃO DA UNIVERSIDADE FEDERAL DO RIO GRANDE\nDO SUL, no uso de suas atribuições, considerando o disposto na Portaria nº 7611, de 29 de setembro de\n2016,  e  tendo  em  vista  o  que  consta  dos  Processos  Administrativos  n°  23078.510719/2016-21  e\n23078.524008/2017-15, do Contrato nº 044/2017, da Lei 10.520/02 e ainda da Lei 8.666/93,\nRESOLVE:\n \nAplicar à Empresa NEVES E ROMANOSKLI LTDA - ME, CNPJ n.º 15.717.915/0001-90, conforme atestado pela\nfiscalização no doc. SEI nº 0817113 e 0925939, bem como pelo NUDECON (doc. SEI nº 1055527) no Processo\n23078.524008/2017-15, as seguintes sanções administrativas:\n \n1. ADVERTÊNCIA, previst

In [140]:
print(df_docs['text'].loc[55505])
df_docs['text'] = df_docs['text'].apply(data_processing.clear_text)
print(df_docs['text'].loc[55505])

Documento gerado sob autenticação Nº RRM.458.680.FGN, disponível no
endereço http://www.ufrgs.br/autenticacao
Documento certificado eletronicamente, conforme Portaria nº
3362/2016, que institui o Sistema de Documentos Eletrônicos da UFRGS.
1/1
PORTARIA Nº             4534                  de  22/06/2018
O PRÓ-REITOR DE PLANEJAMENTO E ADMINISTRAÇÃO DA UNIVERSIDADE FEDERAL DO RIO GRANDE
DO SUL, no uso de suas atribuições, considerando o disposto na Portaria nº 7611, de 29 de setembro de
2016,  e  tendo  em  vista  o  que  consta  dos  Processos  Administrativos  n°  23078.510719/2016-21  e
23078.524008/2017-15, do Contrato nº 044/2017, da Lei 10.520/02 e ainda da Lei 8.666/93,
RESOLVE:
 
Aplicar à Empresa NEVES E ROMANOSKLI LTDA - ME, CNPJ n.º 15.717.915/0001-90, conforme atestado pela
fiscalização no doc. SEI nº 0817113 e 0925939, bem como pelo NUDECON (doc. SEI nº 1055527) no Processo
23078.524008/2017-15, as seguintes sanções administrativas:
 
1. ADVERTÊNCIA, prevista na no item 1 da

#### Sentence tokenization
Having cleaned our documents we will split them into sentences. The **data_processing.split_text_sentences** function will return a DataFrame with: The sentences, a unique ID for each sentence and the index of the document each sentence is a part of.

In [141]:
df_sentences = data_processing.split_text_sentences(df_docs['text'])
pd.set_option("display.max_colwidth", 0)
print(df_sentences.shape)
df_sentences.head()

(2512, 3)


document  \
0  25644      
1  25644      
2  25644      
3  25644      
4  25645      

                                                                                                                                                                                                                                                                                                                                                                                 sentence  \
0  Documento gerado sob autenticação Nº AHX.976.775.357, disponível no endereço http://www.ufrgs.br/autenticacao Documento certificado eletronicamente, conforme Portaria nº 3362/2016, que institui o Sistema de Documentos Eletrônicos da UFRGS.                                                                                                                                          
1  1/1 PORTARIA Nº 5866 de 08/08/2016 O PRÓ-REITOR DE GESTÃO DE PESSOAS DA UNIVERSIDADE FEDERAL DO RIO GRANDE DO SUL, no uso de suas atribuições, considerando o disposto na Portaria nº 5469, de 04 de outubro de 2012 RESOLVE.                                                                                                                                                            
2  Conceder à servidora LISIANE RAMOS VILK, ocupante do cargo de Administrador de Edifícios - 701400, lotada na Faculdade de Arquitetura, SIAPE 2325261, o percentual de 25% (vinte e cinco por cento) de Incentivo à Qualificação, a contar de 15/07/2016, tendo em vista a conclusão do curso de Graduação em Administração - Bacharelado, conforme o Processo nº 23078.015333/2016-19.   
3  MAURÍCIO VIÉGAS DA SILVA Pró-Reitor de Gestão de Pessoas                                                                                                                                                                                                                                                                                                                                 
4  Documento gerado sob autenticação Nº SDG.667.383.ILF, disponível no endereço http://www.ufrgs.br/autenticacao Documento certificado eletronicamente, conforme Portaria nº 3362/2016, que institui o Sistema de Documentos Eletrônicos da UFRGS.                                                                                                                                          

   sentence_id  
0  0            
1  1            
2  2            
3  3            
4  4

#### Dealing with duplicate sentences
Now that we have our dataset of sentences we'll go to the last step which is identifying and categorizing duplicate sentences. Since we need to manually annotate the dataset for training we can group duplicate sentences to facilitate the anottation process. The document we have are fairly standardized so there are a few duplicates we will find.

Let's group sentences by their textual content. Each group will be composed of identical sentences.

In [142]:
test_group = df_sentences.groupby('sentence')

In [143]:
#pd.set_option("display.max_rows", 400)
#test_group.describe()

We loop each group of duplicated sentences and create a dictionary where the key will be the index of the first sentence of the group and the value is the index of all sentences equal to the first.

In [144]:
duplicates = {}
for i in test_group:
    dup_list = i[1]['sentence_id'].tolist()
    duplicates[dup_list[0]] = dup_list


We create a dataframe which will contain only unique sentences. The sentences that have identic pairs will have all of their indexes in a list in the 'duplicates' column. This will allow us to replicate the labels after the anotattion process.

In [145]:
df_unique_sentences = df_sentences.copy()
df_unique_sentences['duplicates'] = pd.Series(duplicates, index=df_sentences.index)
df_unique_sentences = df_unique_sentences.dropna(subset=['duplicates'])
df_unique_sentences['label'] = ""

We can see that the unique dataframe has less sentences which represen the duplicates we removed

In [146]:
pprint(df_sentences.shape)
pprint(df_unique_sentences.shape)

(2512, 3)
(1963, 5)


#### Manual Removal of Bad Sentences
Some sentences are not going to be helpful on our final train and test data. They either have just one or no entities we are interested in. Because of that we'll remove them from our dataset.

In [147]:
pprint(df_unique_sentences.shape)
df_unique_sentences = df_unique_sentences[df_unique_sentences['sentence'].str.len() > 20]
df_unique_sentences = df_unique_sentences[~df_unique_sentences['sentence'].str.startswith("Documento gerado sob")]
df_unique_sentences = df_unique_sentences[~df_unique_sentences['sentence'].str.startswith("Solicitação nº")]
df_unique_sentences = df_unique_sentences[~df_unique_sentences['sentence'].str.startswith("Processo")]
df_unique_sentences = df_unique_sentences[~df_unique_sentences['sentence'].str.contains("RESOLVE")]
pprint(df_unique_sentences.shape)

(1963, 5)
(729, 5)


In [148]:
#pprint(df_unique_sentences.to_json(lines=True, orient = 'records'))
df_docs.to_json(os.path.join(path_to_train, 'ufrgs_documents.jsonl'),lines=True, orient = 'records')
df_unique_sentences.to_json(os.path.join(path_to_train, 'unique_sentences.jsonl'),lines=True, orient = 'records')

#### Assistive Auto Labelling
Before we import our sentences into doccano for manual labelling, we'll use the auto_tagger to automatically label them. This will make it easier to do the manual labelling as a few entities will already be correctly or almost correctly identified.

In [149]:
# Load the auto_tagger model
from transformers import pipeline
assistive_auto_tagger = pipeline(
    "token-classification",
    model='auto_tagger',
    aggregation_strategy="average",
    ignore_labels=[""],
    device=0
)

In [151]:
# Run the sentences through our NER tagging model
df_unique_sentences['tagged_entities'] = df_unique_sentences['sentence'].apply(lambda x: assistive_auto_tagger(x[:512]))

Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.
c:\Users\arthu\anaconda3\envs\NLP22\lib\site-packages\transformers\pipelines\base.py:1043: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(


In [152]:
# Reformat the classified entities text to match the original sentence.
df_unique_sentences['tagged_entities'] = df_unique_sentences.apply(lambda x: data_processing.reformat_sentence(x['sentence'], x['tagged_entities']), axis=1)

Conceder à servidora
C C
o o
n n
c c
e e
d d
e e
r r
   
à à
   
s s
e e
r r
v v
i i
d d
o o
r r
a a
LISIANE RAMOS VILK
L  
Bad char: L
I I
S S
I I
A A
N N
E E
   
R R
A A
M M
O O
S S
   
V V
I I
L L
K K
, ocupante do cargo de Administrador de Edifícios - 701400, lotada na Faculdade de Arquitetura, SIAPE 2325261, o percentual de 25 % ( vinte e cinco por cento ) de Incentivo à Qualificação, a contar de 15 / 07 / 2016, tendo em vista a conclusão do curso de Graduação em Administração - Bacharelado, conforme o Processo nº 23078. 015333 / 2016 - 19.
, ,
   
o o
c c
u u
p p
a a
n n
t t
e e
   
d d
o o
   
c c
a a
r r
g g
o o
   
d d
e e
   
A A
d d
m m
i i
n n
i i
s s
t t
r r
a a
d d
o o
r r
   
d d
e e
   
E E
d d
i i
f f
í í
c c
i i
o o
s s
   
- -
   
7 7
0 0
1 1
4 4
0 0
0 0
, ,
   
l l
o o
t t
a a
d d
a a
   
n n
a a
   
F F
a a
c c
u u
l l
d d
a a
d d
e e
   
d d
e e
   
A A
r r
q q
u u
i i
t t
e e
t t
u u
r r
a a
, ,
   
S S
I I
A A
P P
E E
   
2 2
3 3
2 2
5 5
2 2
6 6
1 1
, ,
   
o o


In [18]:
df_unique_sentences.head(10)

document  \
2   25644      
3   25644      
6   25645      
8   25645      
11  25646      
16  25647      
21  25648      
26  25649      
31  25652      
33  25652      

                                                                                                                                                                                                                                                                                                                                                                                                                                                                          sentence  \
2   Conceder à servidora LISIANE RAMOS VILK, ocupante do cargo de Administrador de Edifícios - 701400, lotada na Faculdade de Arquitetura, SIAPE 2325261, o percentual de 25% (vinte e cinco por cento) de Incentivo à Qualificação, a contar de 15/07/2016, tendo em vista a conclusão do curso de Graduação em Administração - Bacharelado, conforme o Processo nº 23078.015333/2016-19.                                                                                           
3   MAURÍCIO VIÉGAS DA SILVA Pró-Reitor de Gestão de Pessoas                                                                                                                                                                                                                                                                                                                                                                                                                         
6   Autorizar o afastamento do país de CRISTINE MARIA WARMLING, Professor do Magistério Superior, lotada e em exercício no Departamento de Odontologia Preventiva e Social da Faculdade de Odontologia, com a finalidade de participar do "3ème Congrès de la Societé Internationale d'Ergologie", em Aix-en-Provence - França, no período compreendido entre 28/08/2016 e 01/09/2016, com ônus limitado.                                                                            
8   CARLOS ALEXANDRE NETTO Reitor                                                                                                                                                                                                                                                                                                                                                                                                                                                    
11  Autorizar o afastamento do país de ANDRE DIAS MORTARI, Assistente em Administração, lotado e em exercício na Escola de Administração, com a finalidade de participar do "IV Congreso Internacional Red Pilares", em Cartagena - Colombia, no período compreendido entre 29/08/2016 e 02/09/2016, com ônus limitado.                                                                                                                                                              
16  Autorizar o afastamento do país de RAFAEL ROESLER, Professor do Maigstério Superior, lotado e em exercício no Departamento de Farmacologia do Instituto de Ciências Básicas da Saúde, com a finalidade de participar de reunião na University of Nottingham - Inglaterra, no período compreendido entre 02/09/2016 e 10/09/2016, com limitado.                                                                                                                                   
21  Autorizar o afastamento do país de HUGO VERLI, Professor do Magistério Superior, lotado e em exercício no Departamento de Biologia Molecular e Biotecnologia do Instituto de Biociências, com a finalidade de participar de reunião na University of Nottingham - Inglaterra, no período compreendido entre 02/09/2016 e 09/09/2016, com ônus limitado.                                                                                                                          
26  Autorizar o afastamento do país de ANGELA TEREZINHA DE SOUZA WY